In [69]:
import dash
import dash_bootstrap_components as dbc
import dash_html_components as html
import dash_core_components as dcc
import pandas as pd
import plotly.express as px
import data_cleaning
import plotly.graph_objects as go

app = dash.Dash(external_stylesheets=[dbc.themes.BOOTSTRAP])

# Load df dataset
df = data_cleaning.main()
df = data_cleaning.as_type(df, 'int', 'TOTAL_HOUSEHOLD_INCOME_-_CURRENT_DOLLARS')
df = data_cleaning.as_type(df, 'int', 'AGE_OF_RESPONDENT')
#create first figure
df_group = df.groupby('AGE_OF_RESPONDENT')['TOTAL_HOUSEHOLD_INCOME_-_CURRENT_DOLLARS'].mean().reset_index()
df_group = pd.DataFrame(df_group)
df_group = df_group[['AGE_OF_RESPONDENT', 'TOTAL_HOUSEHOLD_INCOME_-_CURRENT_DOLLARS']].sort_values(by='AGE_OF_RESPONDENT',ascending=True)
#create second figure
df_fin = df[(df["PERSONAL_FINANCES_B/W_YEAR_AGO"] != 9) & (df["PERSONAL_FINANCES_B/W_NEXT_YEAR"] != 9)]
df_fin = df_fin[df_fin["PERSONAL_FINANCES_B/W_YEAR_AGO"].isin([1, 3, 5, 8])]
df_fin = df_fin[df_fin["PERSONAL_FINANCES_B/W_NEXT_YEAR"].isin([1, 3, 5, 8])]
df_count_pexp = df_fin["PERSONAL_FINANCES_B/W_NEXT_YEAR"].value_counts().sort_index()
df_count_pago = df_fin["PERSONAL_FINANCES_B/W_YEAR_AGO"].value_counts().sort_index()


# Define dropdown options
dropdown_options = {
    'AGE_OF_RESPONDENT': 'Age',
    'REGION_OF_RESIDENCE': 'Region of Residence',
    'SEX_OF_RESPONDENT': 'Sex',
    'MARITAL_STATUS_OF_RESPONDENT': 'Marital Status'
}

# Define groupby options
groupby_options = {
    'EDUCATION_OF_RESPONDENT': 'Education level',
    'EDUCATION:_COLLEGE_GRADUATE': 'Education: college grad',
    'POLITICAL_AFFILIATION': 'Political Affiliation'
}

# Define function to create data table
def create_table(df):
    return dbc.Table.from_dataframe(df, striped=True, bordered=True, hover=True)

# Define app layout
app.layout = dbc.Container([
    dbc.Row([
        dbc.Col([
            html.H1('df Dashboard', className='text-center'),
            html.Hr(),
            html.H4('Select X-Axis'),
            dcc.Dropdown(
                id='dropdown-x',
                options=[{'label': label, 'value': value} for value, label in dropdown_options.items()],
                value='AGE_OF_RESPONDENT'
            ),
            html.H4('Select Group By'),
            dcc.Dropdown(
                id='dropdown-groupby',
                options=[{'label': label, 'value': value} for value, label in groupby_options.items()],
                value='EDUCATION_OF_RESPONDENT'
            ),
        ], md=4),
        dbc.Col([
            dcc.Tabs([
                dcc.Tab(label='Table', value='table'),
                dcc.Tab(label='Graph', value='graph'),
            ], id='tabs', value='table'),
            html.Div(id='display-page'),
        ], md=8)
    ])
])

# Define callback to update display page
@app.callback(
    dash.dependencies.Output('display-page', 'children'),
    [dash.dependencies.Input('dropdown-x', 'value'),
     dash.dependencies.Input('dropdown-groupby', 'value'),
     dash.dependencies.Input('tabs', 'value')]
)
def display_page(x, groupby, tab):
    # Compute groupby
    if tab == 'table':
        # Create data table
        df_grouped = df.groupby(groupby)[x].describe().reset_index()
        table = create_table(df_grouped)
        # Return table
        return table
    elif tab == 'graph':
        # Create four static graphs
        fig1 = px.line(df_group, x='AGE_OF_RESPONDENT', y='TOTAL_HOUSEHOLD_INCOME_-_CURRENT_DOLLARS', title='Total Income Based on Age')
        fig2 = px.bar(df_fin, x='AGE_OF_RESPONDENT', y='PERSONAL_FINANCES_B/W_NEXT_YEAR')

        #Return a list of the four graphs
        return [dcc.Graph(figure=fig1)], #dcc.Graph(figure=fig2)#, dcc.Graph(figure=fig3), dcc.Graph(figure=fig4)
if __name__ == '__main__':
    app.run_server(port=8888)

c:\Users\e707088\OneDrive - Blue Cross Blue Shield of Michigan\Documents\Python\final_project\data_cleaning.py:13: DtypeWarning:

Columns (13,15,16,18,32,34,36,37,41,45,46,55,71,83,84,86,87,90,91,92,96,98,100,101,103,104,105,106,107,108,109) have mixed types. Specify dtype option on import or set low_memory=False.



Dash is running on http://127.0.0.1:8888/

 * Serving Flask app "__main__" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://127.0.0.1:8888/ (Press CTRL+C to quit)


In [70]:
px.bar(df_fin, x='AGE_OF_RESPONDENT', y='PERSONAL_FINANCES_B/W_NEXT_YEAR')

In [71]:
df_group.columns

Index(['AGE_OF_RESPONDENT', 'TOTAL_HOUSEHOLD_INCOME_-_CURRENT_DOLLARS'], dtype='object')

AGE_OF_RESPONDENT  TOTAL_HOUSEHOLD_INCOME_-_CURRENT_DOLLARS
0                  18                              47242.234808
1                  19                              44581.926061
2                  20                              42073.470460
3                  21                              37207.997260
4                  22                              36864.856170
..                ...                                       ...
75                 93                              36676.476190
76                 94                              26794.000000
77                 95                              34986.941176
78                 96                              51317.739130
79                 97                              32701.469388

[80 rows x 2 columns]